# Checking Embeddings of Terms (Noun/Verb/Adj/etc.) from Tagged Wordnet Gloss

I discovered there's a more active fork of wordnet and bumped this analysis over to that.

In [ ]:
!pip install datasets

In [ ]:
from datasets import load_dataset

# Load the dataset
dataset = load_dataset("jon-tow/open-english-wordnet-synset-2023")

In [ ]:
dataset['train'][0]

{'@id': 'oewn-03159292-a',
 '@ili': 'i18097',
 '@members': 'oewn-avenged-a',
 '@partOfSpeech': 'a',
 '@lexfile': 'adj.ppl',
 'Definition': 'for which vengeance has been taken',
 'SynsetRelation': [],
 'Example': 'an avenged injury',
 'ILIDefinition': None,
 '@dc:source': None}

In [ ]:
import pandas as pd

In [ ]:
df = pd.DataFrame(dataset['train'])

In [ ]:
df.head()

@id    @ili                            @members @partOfSpeech  \
0  oewn-03159292-a  i18097                      oewn-avenged-a             a   
1  oewn-03159419-a  i18098                    oewn-unavenged-a             a   
2  oewn-03159554-a  i18099                       oewn-beaten-a             a   
3  oewn-03159654-a  i18100  oewn-calibrated-a oewn-graduated-a             a   
4  oewn-03159804-a  i18101                    oewn-cantering-a             a   

  @lexfile                                    Definition SynsetRelation  \
0  adj.ppl            for which vengeance has been taken             []   
1  adj.ppl        for which vengeance has not been taken             []   
2  adj.ppl              formed or made thin by hammering             []   
3  adj.ppl           marked with or divided into degrees             []   
4  adj.ppl  riding at a gait between a trot and a gallop             []   

                    Example ILIDefinition @dc:source  
0         an avenged injury          None       None  
1       an unavenged murder          None       None  
2               beaten gold          None       None  
3  a calibrated thermometer          None       None  
4    the cantering soldiers          None       None

Getting the @members into a reasonable format is about to take a bunch of cells and most of my patience for the day.

In [ ]:
df.shape

(120135, 10)

In [ ]:
df[['@members', '@partOfSpeech', '@lexfile']].head()

@members @partOfSpeech @lexfile
0                      oewn-avenged-a             a  adj.ppl
1                    oewn-unavenged-a             a  adj.ppl
2                       oewn-beaten-a             a  adj.ppl
3  oewn-calibrated-a oewn-graduated-a             a  adj.ppl
4                    oewn-cantering-a             a  adj.ppl

In [ ]:
df = df[['@members', '@partOfSpeech', '@lexfile']]

In [ ]:
pattern = r'^(\w+-\w+-\w+ *)*$'

matches_pattern = df['@members'].str.match(pattern)

all_match_pattern = matches_pattern.all()
all_match_pattern

False

In [ ]:
members_not_matching_pattern = df[~matches_pattern]
members_not_matching_pattern

@members @partOfSpeech  \
13                       oewn-hand-held-a oewn-handheld-a             a   
42                                      oewn-re-created-a             a   
49                                     oewn-spray-dried-a             a   
57                                oewn-closed-captioned-a             a   
116     oewn-plane_figure-n oewn-two-dimensional_figure-n             n   
...                                                   ...           ...   
119954  oewn-real-time_processing-n oewn-real-time_ope...             n   
119976                   oewn-reuptake-n oewn-re-uptake-n             n   
120005  oewn-slump-n oewn-slack-n oewn-drop-off-n oewn...             n   
120123  oewn-constant-volume_process-n oewn-isometric_...             n   
120127     oewn-anti-selection-n oewn-adverse_selection-n             n   

            @lexfile  
13           adj.ppl  
42           adj.ppl  
49           adj.ppl  
57           adj.ppl  
116       noun.shape  
...              ...  
119954  noun.process  
119976  noun.process  
120005  noun.process  
120123  noun.process  
120127  noun.process  

[6987 rows x 3 columns]

In [ ]:
pattern = r'^(\w+-[\w_\-.]+-\w+ *)*$' # This took a couple of iterations not represented

matches_pattern = df['@members'].str.match(pattern)

all_match_pattern = matches_pattern.all()
all_match_pattern

True

In [ ]:
# I found this problem later on
oddball = df['@members'].str.match('.*Gravenhage.*')
oddball_member = df[oddball]['@members']

In [ ]:
oddball_member.iloc[0]

'oewn-The_Hague-n oewn--ap-s_Gravenhage-n oewn-Den_Haag-n'

In [ ]:
df = df.assign(members=df['@members'].str.split()).explode('members')

In [ ]:
df.head()

@members @partOfSpeech @lexfile  \
0                      oewn-avenged-a             a  adj.ppl   
1                    oewn-unavenged-a             a  adj.ppl   
2                       oewn-beaten-a             a  adj.ppl   
3  oewn-calibrated-a oewn-graduated-a             a  adj.ppl   
3  oewn-calibrated-a oewn-graduated-a             a  adj.ppl   

             members  
0     oewn-avenged-a  
1   oewn-unavenged-a  
2      oewn-beaten-a  
3  oewn-calibrated-a  
3   oewn-graduated-a

In [ ]:
df.shape

(212071, 4)

In [ ]:
prefixes = df['members'].str.split('-', expand=True)[0]
prefix_freq = prefixes.value_counts().reset_index()
prefix_freq.columns = ['Prefix', 'Frequency']

prefix_freq = prefix_freq.sort_values(by='Frequency', ascending=False)

print(prefix_freq)

  Prefix  Frequency
0   oewn     212071


In [ ]:
to_remove = 'oewn-'

df['members'] = df['members'].apply(lambda x: x.replace(to_remove, '') if x.startswith(to_remove) else x)

In [ ]:
prefixes = df['members'].str.split('-', expand=True)[0]
prefix_freq = prefixes.value_counts().reset_index()
prefix_freq.columns = ['Prefix', 'Frequency']

prefix_freq = prefix_freq.sort_values(by='Frequency', ascending=False)

print(prefix_freq)

                                                Prefix  Frequency
0                                                 self        252
1                                                 high        102
2                                                 well         98
3                                                  one         85
4                                                  cut         79
...                                                ...        ...
66494                                              CIA          1
66493   National_Institute_of_Standards_and_Technology          1
66492                          Counterterrorist_Center          1
66491                          Nonproliferation_Center          1
145809                            grammatical_cohesion          1

[145810 rows x 2 columns]


In [ ]:
# Check for values starting with "-"
values_starting_with_dash = df[df['members'].str.startswith('-')]

# Display the values starting with "-"
print(values_starting_with_dash)

                                                 @members @partOfSpeech  \
81633   oewn-The_Hague-n oewn--ap-s_Gravenhage-n oewn-...             n   
106115                    oewn-between-r oewn--ap-tween-r             r   
107858        oewn-between_decks-r oewn--ap-tween_decks-r             r   
114349                        oewn-hood-n oewn--ap-hood-n             n   

             @lexfile             members  
81633   noun.location  -ap-s_Gravenhage-n  
106115        adv.all         -ap-tween-r  
107858        adv.all   -ap-tween_decks-r  
114349     noun.group          -ap-hood-n  


In [ ]:
df.head()

@members @partOfSpeech @lexfile       members
0                      oewn-avenged-a             a  adj.ppl     avenged-a
1                    oewn-unavenged-a             a  adj.ppl   unavenged-a
2                       oewn-beaten-a             a  adj.ppl      beaten-a
3  oewn-calibrated-a oewn-graduated-a             a  adj.ppl  calibrated-a
3  oewn-calibrated-a oewn-graduated-a             a  adj.ppl   graduated-a

In [ ]:
df['members'] = df['members'].apply(lambda x: x[4:] if x.startswith('-ap-') else x)

In [ ]:
df.drop(columns=['@members'], inplace=True)

In [ ]:
suffixes = df['members'].str.split('-').str[-1]

# Count frequencies of suffixes
suffix_freq = suffixes.value_counts().reset_index()
suffix_freq.columns = ['Suffix', 'Frequency']

# Sort by frequency
suffix_freq = suffix_freq.sort_values(by='Frequency', ascending=False)

# Display suffixes ordered by frequency
print(suffix_freq[:40])

  Suffix  Frequency
0      n     151001
1      a      30150
2      v      25098
3      r       5595
4      1        146
5      2         69
6      s         12


In [ ]:
filtered_df = df[df['members'].str.endswith(('1', '2', 's'))]

print(filtered_df)

       @partOfSpeech            @lexfile      members
286                n          noun.shape     lead-n-1
301                n          noun.shape      bow-n-1
325                n          noun.shape    tower-n-1
782                s             adj.all   panelled-s
2303               s             adj.all     centre-s
...              ...                 ...          ...
117472             v           verb.body     tear-v-2
117596             v           verb.body  recover-v-1
118299             v  verb.communication      bow-v-1
118397             v  verb.communication      bow-v-1
118473             v  verb.communication    whoop-v-1

[227 rows x 3 columns]


In [ ]:
df['members'] = df['members'].apply(lambda x: x.replace('-ap-', "'")) # They use this for apostrophe for some reason, probably because it was stored as yaml

In [ ]:
# List of suffixes to remove
suffixes_to_remove = ['-n', '-a', '-v', '-r', '-1', '-2', '-s']

# Function to remove suffixes
def remove_suffixes(member):
    # Iterate until no suffixes are left
    while any(member.endswith(suffix) for suffix in suffixes_to_remove):
        for suffix in suffixes_to_remove:
            if member.endswith(suffix):
                member = member[:-len(suffix)]  # Remove the suffix
    return member

# Apply the function to each member in the DataFrame
df['members'] = df['members'].apply(remove_suffixes)

# Display the updated DataFrame
df.head()

@partOfSpeech @lexfile     members
0             a  adj.ppl     avenged
1             a  adj.ppl   unavenged
2             a  adj.ppl      beaten
3             a  adj.ppl  calibrated
3             a  adj.ppl   graduated

In [ ]:
df['members'] = df['members'].apply(lambda x: " ".join(x.split("_")))

In [ ]:
df.head()

@partOfSpeech @lexfile     members
0             a  adj.ppl     avenged
1             a  adj.ppl   unavenged
2             a  adj.ppl      beaten
3             a  adj.ppl  calibrated
3             a  adj.ppl   graduated

In [ ]:
pd.get_dummies(df['@partOfSpeech'])

a  n  r  s  v
0       1  0  0  0  0
1       1  0  0  0  0
2       1  0  0  0  0
3       1  0  0  0  0
3       1  0  0  0  0
...    .. .. .. .. ..
120130  0  1  0  0  0
120131  0  1  0  0  0
120132  0  1  0  0  0
120133  0  1  0  0  0
120134  0  1  0  0  0

[212071 rows x 5 columns]

In [ ]:
pd.get_dummies(df['@lexfile'])

adj.all  adj.pert  adj.ppl  adv.all  noun.Tops  noun.act  noun.animal  \
0             0         0        1        0          0         0            0   
1             0         0        1        0          0         0            0   
2             0         0        1        0          0         0            0   
3             0         0        1        0          0         0            0   
3             0         0        1        0          0         0            0   
...         ...       ...      ...      ...        ...       ...          ...   
120130        0         0        0        0          0         0            0   
120131        0         0        0        0          0         0            0   
120132        0         0        0        0          0         0            0   
120133        0         0        0        0          0         0            0   
120134        0         0        0        0          0         0            0   

        noun.artifact  noun.attribute  noun.body  ...  verb.consumption  \
0                   0               0          0  ...                 0   
1                   0               0          0  ...                 0   
2                   0               0          0  ...                 0   
3                   0               0          0  ...                 0   
3                   0               0          0  ...                 0   
...               ...             ...        ...  ...               ...   
120130              0               0          0  ...                 0   
120131              0               0          0  ...                 0   
120132              0               0          0  ...                 0   
120133              0               0          0  ...                 0   
120134              0               0          0  ...                 0   

        verb.contact  verb.creation  verb.emotion  verb.motion  \
0                  0              0             0            0   
1                  0              0             0            0   
2                  0              0             0            0   
3                  0              0             0            0   
3                  0              0             0            0   
...              ...            ...           ...          ...   
120130             0              0             0            0   
120131             0              0             0            0   
120132             0              0             0            0   
120133             0              0             0            0   
120134             0              0             0            0   

        verb.perception  verb.possession  verb.social  verb.stative  \
0                     0                0            0             0   
1                     0                0            0             0   
2                     0                0            0             0   
3                     0                0            0             0   
3                     0                0            0             0   
...                 ...              ...          ...           ...   
120130                0                0            0             0   
120131                0                0            0             0   
120132                0                0            0             0   
120133                0                0            0             0   
120134                0                0            0             0   

        verb.weather  
0                  0  
1                  0  
2                  0  
3                  0  
3                  0  
...              ...  
120130             0  
120131             0  
120132             0  
120133             0  
120134             0  

[212071 rows x 45 columns]

In [ ]:
df_to_upload = pd.concat([df['members'], pd.get_dummies(df['@partOfSpeech'])], axis=1)
df_to_upload = pd.concat([df_to_upload, pd.get_dummies(df['@lexfile'])], axis=1)

In [ ]:
df_to_upload

members  a  n  r  s  v  adj.all  adj.pert  adj.ppl  \
0                    avenged  1  0  0  0  0        0         0        1   
1                  unavenged  1  0  0  0  0        0         0        1   
2                     beaten  1  0  0  0  0        0         0        1   
3                 calibrated  1  0  0  0  0        0         0        1   
3                  graduated  1  0  0  0  0        0         0        1   
...                      ... .. .. .. .. ..      ...       ...      ...   
120130       bromoil process  0  1  0  0  0        0         0        0   
120131         interfixation  0  1  0  0  0        0         0        0   
120132    consonant mutation  0  1  0  0  0        0         0        0   
120133              cohesion  0  1  0  0  0        0         0        0   
120134  grammatical cohesion  0  1  0  0  0        0         0        0   

        adv.all  ...  verb.consumption  verb.contact  verb.creation  \
0             0  ...                 0             0              0   
1             0  ...                 0             0              0   
2             0  ...                 0             0              0   
3             0  ...                 0             0              0   
3             0  ...                 0             0              0   
...         ...  ...               ...           ...            ...   
120130        0  ...                 0             0              0   
120131        0  ...                 0             0              0   
120132        0  ...                 0             0              0   
120133        0  ...                 0             0              0   
120134        0  ...                 0             0              0   

        verb.emotion  verb.motion  verb.perception  verb.possession  \
0                  0            0                0                0   
1                  0            0                0                0   
2                  0            0                0                0   
3                  0            0                0                0   
3                  0            0                0                0   
...              ...          ...              ...              ...   
120130             0            0                0                0   
120131             0            0                0                0   
120132             0            0                0                0   
120133             0            0                0                0   
120134             0            0                0                0   

        verb.social  verb.stative  verb.weather  
0                 0             0             0  
1                 0             0             0  
2                 0             0             0  
3                 0             0             0  
3                 0             0             0  
...             ...           ...           ...  
120130            0             0             0  
120131            0             0             0  
120132            0             0             0  
120133            0             0             0  
120134            0             0             0  

[212071 rows x 51 columns]

In [ ]:
df_to_upload.head()

members  a  n  r  s  v  adj.all  adj.pert  adj.ppl  adv.all  ...  \
0     avenged  1  0  0  0  0        0         0        1        0  ...   
1   unavenged  1  0  0  0  0        0         0        1        0  ...   
2      beaten  1  0  0  0  0        0         0        1        0  ...   
3  calibrated  1  0  0  0  0        0         0        1        0  ...   
3   graduated  1  0  0  0  0        0         0        1        0  ...   

   verb.consumption  verb.contact  verb.creation  verb.emotion  verb.motion  \
0                 0             0              0             0            0   
1                 0             0              0             0            0   
2                 0             0              0             0            0   
3                 0             0              0             0            0   
3                 0             0              0             0            0   

   verb.perception  verb.possession  verb.social  verb.stative  verb.weather  
0                0                0            0             0             0  
1                0                0            0             0             0  
2                0                0            0             0             0  
3                0                0            0             0             0  
3                0                0            0             0             0  

[5 rows x 51 columns]

In [ ]:
df_to_upload = df_to_upload.groupby('members').max().reset_index()


In [ ]:
df_to_upload

members  a  n  r  s  v  adj.all  adj.pert  adj.ppl  adv.all  ...  \
0               .22  0  1  0  0  0        0         0        0        0  ...   
1       .22 caliber  1  0  0  0  0        0         1        0        0  ...   
2       .22 calibre  1  0  0  0  0        0         1        0        0  ...   
3       .22-caliber  1  0  0  0  0        0         1        0        0  ...   
4       .22-calibre  1  0  0  0  0        0         1        0        0  ...   
...             ... .. .. .. .. ..      ...       ...      ...      ...  ...   
153356    zymolysis  0  1  0  0  0        0         0        0        0  ...   
153357    zymolytic  1  0  0  0  0        0         1        0        0  ...   
153358      zymosis  0  1  0  0  0        0         0        0        0  ...   
153359      zymotic  1  0  0  0  0        0         1        0        0  ...   
153360      zymurgy  0  1  0  0  0        0         0        0        0  ...   

        verb.consumption  verb.contact  verb.creation  verb.emotion  \
0                      0             0              0             0   
1                      0             0              0             0   
2                      0             0              0             0   
3                      0             0              0             0   
4                      0             0              0             0   
...                  ...           ...            ...           ...   
153356                 0             0              0             0   
153357                 0             0              0             0   
153358                 0             0              0             0   
153359                 0             0              0             0   
153360                 0             0              0             0   

        verb.motion  verb.perception  verb.possession  verb.social  \
0                 0                0                0            0   
1                 0                0                0            0   
2                 0                0                0            0   
3                 0                0                0            0   
4                 0                0                0            0   
...             ...              ...              ...          ...   
153356            0                0                0            0   
153357            0                0                0            0   
153358            0                0                0            0   
153359            0                0                0            0   
153360            0                0                0            0   

        verb.stative  verb.weather  
0                  0             0  
1                  0             0  
2                  0             0  
3                  0             0  
4                  0             0  
...              ...           ...  
153356             0             0  
153357             0             0  
153358             0             0  
153359             0             0  
153360             0             0  

[153361 rows x 51 columns]

In [ ]:
df_to_upload.to_csv("openwordnet-categoricals.csv", index=False)